# Capstone Project

The objective of this study is to use data science tools to help a tourist agency to determine a new travel package for their customers. Our job as data scientists is to give the agency multiple travel package options so they can sell them to their customers; these options will be presented by comparing New York and Los Angeles (what makes them different) and what different activities you can do in each city.    

## Extracting the data we will be using

First, we need to import all the libraries that we will be using in our project

In [2]:
import numpy as np 
import pandas as pd 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json 
!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim 
import requests 
from pandas.io.json import json_normalize 
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
!conda install -c conda-forge folium=0.5.0 --yes 
import folium

print('Libraries imported.')

Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.5.11
  latest version: 4.7.10

Please update conda by running

    $ conda update -n base -c defaults conda



# All requested packages already installed.

Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.5.11
  latest version: 4.7.10

Please update conda by running

    $ conda update -n base -c defaults conda



# All requested packages already installed.

Libraries imported.


#### This is the New York dataset 

In [3]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset

In [4]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

Now we can create the DataFrame

In [5]:
neighborhoods_data = newyork_data['features']
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 
neighborhoods = pd.DataFrame(columns=column_names)
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [6]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [56]:
neighborhoods.dtypes

Borough          object
Neighborhood     object
Latitude        float64
Longitude       float64
dtype: object

## LA data

In [66]:
LA_data = pd.read_csv('LA.csv')

In [67]:
LA_data.head()

Borough        Neighborhood   Latitude   Longitude
0  Downtown Los Angeles            Chinatown  34.064989 -118.237295
1  Downtown Los Angeles         Civic Center  34.056096 -118.244619
2  Downtown Los Angeles     Fashion District  34.037529 -118.250216
3  Downtown Los Angeles   Financial District  34.048893 -118.258459
4  Downtown Los Angeles        Historic Core  34.044376 -118.251475

In [73]:
pd.set_option("display.precision", 8)
df = pd.DataFrame()
df['Borough'] = LA_data['Borough']
df['Neighborhood'] = LA_data['Neighborhood']
df['Latitude'] = LA_data['Latitude']
df['Longitude'] = LA_data['Longitude']
df.dtypes

Borough          object
Neighborhood     object
Latitude        float64
Longitude       float64
dtype: object

### Now lets use Foursquare for both New York and LA

In [60]:
CLIENT_ID = '30YXV4OFB0Z5TOADL41EA1ZMIYLRZP1WCLLORLTIFKSSKOG0' 
CLIENT_SECRET = 'D1EXCXMGIVGIMJWVNA0WO2FJCANOFYJGY0ZAPZG1GX3I5EAU' 
VERSION = '20180605' 
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 30YXV4OFB0Z5TOADL41EA1ZMIYLRZP1WCLLORLTIFKSSKOG0
CLIENT_SECRET:D1EXCXMGIVGIMJWVNA0WO2FJCANOFYJGY0ZAPZG1GX3I5EAU


In the code below, I limited the near venues to 10 because tourists usually don't visit many nearby places due to the fact that they like to go to various places in one day. 

In [21]:
LIMIT = 10
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [22]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [23]:
venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [24]:
print(venues.shape)
venues.head()

(2769, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield            40.89470518            -73.84720052   
1    Wakefield            40.89470518            -73.84720052   
2    Wakefield            40.89470518            -73.84720052   
3    Wakefield            40.89470518            -73.84720052   
4    Wakefield            40.89470518            -73.84720052   

                                     Venue  Venue Latitude  Venue Longitude  \
0                         Lollipops Gelato     40.89412315     -73.84589162   
1                                 Rite Aid     40.89664900     -73.84484610   
2                         Carvel Ice Cream     40.89048669     -73.84856773   
3  Cooler Runnings Jamaican Restaurant Inc     40.89827622     -73.85038105   
4                                  Dunkin'     40.89045878     -73.84908887   

         Venue Category  
0          Dessert Shop  
1              Pharmacy  
2        Ice Cream Shop  
3  Caribbean Restaurant  
4            Donut Shop

In [25]:
venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      10                      10   
Annadale                                      10                      10   
Arden Heights                                  4                       4   
Arlington                                      5                       5   
Arrochar                                      10                      10   
Arverne                                       10                      10   
Astoria                                       10                      10   
Astoria Heights                               10                      10   
Auburndale                                    10                      10   
Bath Beach                                    10                      10   
Battery Park City                             10                      10   
Bay Ridge                                     10                      10   
Bay Terrace                                   20                      20   
Baychester                                    10                      10   
Bayside                                       10                      10   
Bayswater                                      2                       2   
Bedford Park                                  10                      10   
Bedford Stuyvesant                            10                      10   
Beechhurst                                    10                      10   
Bellaire                                      10                      10   
Belle Harbor                                  10                      10   
Bellerose                                     10                      10   
Belmont                                       10                      10   
Bensonhurst                                   10                      10   
Bergen Beach                                   7                       7   
Blissville                                    10                      10   
Bloomfield                                     5                       5   
Boerum Hill                                   10                      10   
Borough Park                                  10                      10   
Breezy Point                                   5                       5   
Briarwood                                      8                       8   
Brighton Beach                                10                      10   
Broad Channel                                  7                       7   
Broadway Junction                             10                      10   
Bronxdale                                     10                      10   
Brooklyn Heights                              10                      10   
Brookville                                     2                       2   
Brownsville                                   10                      10   
Bulls Head                                    10                      10   
Bushwick                                      10                      10   
Butler Manor                                   6                       6   
Cambria Heights                               10                      10   
Canarsie                                       6                       6   
Carnegie Hill                                 10                      10   
Carroll Gardens                               10                      10   
Castle Hill                                    8                       8   
Castleton Corners                             10                      10   
Central Harlem                                10                      10   
Charleston                                    10                      10   
Chelsea                                       14                      14   
Chinatown                                     10                      10   

In [27]:

ny_onehot = pd.get_dummies(venues[['Venue Category']], prefix="", prefix_sep="")


ny_onehot['Neighborhood'] = venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [ny_onehot.columns[-1]] + list(ny_onehot.columns[:-1])
nyn_onehot = nyn_onehot[fixed_columns]

ny_onehot.head()

Accessories Store  Adult Boutique  Afghan Restaurant  African Restaurant  \
0                  0               0                  0                   0   
1                  0               0                  0                   0   
2                  0               0                  0                   0   
3                  0               0                  0                   0   
4                  0               0                  0                   0   

   American Restaurant  Antique Shop  Arcade  Arepa Restaurant  \
0                    0             0       0                 0   
1                    0             0       0                 0   
2                    0             0       0                 0   
3                    0             0       0                 0   
4                    0             0       0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Automotive Shop  BBQ Joint  \
0                 0                   0                0          0   
1                 0                   0                0          0   
2                 0                   0                0          0   
3                 0                   0                0          0   
4                 0                   0                0          0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Court  Beach  Beach Bar  Beer Bar  Beer Garden  Beer Store  \
0                 0      0          0         0            0           0   
1                 0      0          0         0            0           0   
2                 0      0          0         0            0           0   
3                 0      0          0         0            0           0   
4                 0      0          0         0            0           0   

   Big Box Store  Bike Trail  Bistro  Board Shop  Boat or Ferry  Bookstore  \
0              0           0       0           0              0          0   
1              0           0       0           0              0          0   
2              0           0       0           0              0          0   
3              0           0       0           0              0          0   
4              0           0       0           0              0          0   

   Boutique  Bowling Alley  Boxing Gym  Brazilian Restaurant  Breakfast Spot  \
0         0              0           0                     0               0   
1         0              0           0                     0               0   
2         0              0           0                     0               0   
3         0              0           0                     0               0   
4         0              0           0                     0               0   

   Brewery  Bridge  Bubble Tea Shop  Building  Burger Joint  Burrito Place  \
0        0       0                0         0             0              0   
1        0       0                0         0             0              0   
2        0       0                0         0             0              0   
3        0       0                0         0             0              0   
4        0       0                0

In [28]:
ny_grouped = ny_onehot.groupby('Neighborhood').mean().reset_index()
ny_grouped

Neighborhood  Accessories Store  Adult Boutique  \
0                     Allerton                0.0             0.0   
1                     Annadale                0.0             0.0   
2                Arden Heights                0.0             0.0   
3                    Arlington                0.0             0.0   
4                     Arrochar                0.0             0.0   
5                      Arverne                0.0             0.0   
6                      Astoria                0.0             0.0   
7              Astoria Heights                0.0             0.0   
8                   Auburndale                0.0             0.0   
9                   Bath Beach                0.0             0.0   
10           Battery Park City                0.0             0.0   
11                   Bay Ridge                0.0             0.0   
12                 Bay Terrace                0.0             0.0   
13                  Baychester                0.0             0.0   
14                     Bayside                0.0             0.0   
15                   Bayswater                0.0             0.0   
16                Bedford Park                0.0             0.0   
17          Bedford Stuyvesant                0.0             0.0   
18                  Beechhurst                0.0             0.0   
19                    Bellaire                0.0             0.0   
20                Belle Harbor                0.0             0.0   
21                   Bellerose                0.0             0.0   
22                     Belmont                0.0             0.0   
23                 Bensonhurst                0.0             0.0   
24                Bergen Beach                0.0             0.0   
25                  Blissville                0.0             0.0   
26                  Bloomfield                0.0             0.0   
27                 Boerum Hill                0.0             0.0   
28                Borough Park                0.0             0.0   
29                Breezy Point                0.0             0.0   
30                   Briarwood                0.0             0.0   
31              Brighton Beach                0.0             0.0   
32               Broad Channel                0.0             0.0   
33           Broadway Junction                0.0             0.0   
34                   Bronxdale                0.0             0.0   
35            Brooklyn Heights                0.0             0.0   
36                  Brookville                0.0             0.0   
37                 Brownsville                0.0             0.0   
38                  Bulls Head                0.0             0.0   
39                    Bushwick                0.0             0.0   
40                Butler Manor                0.0             0.0   
41             Cambria Heights                0.0             0.0   
42                    Canarsie                0.0             0.0   
43               Carnegie Hill                0.0             0.0   
44             Carroll Gardens                0.0             0.0   
45                 Castle Hill                0.0             0.0   
46           Castleton Corners                0.0             0.0   
47              Central Harlem                0.0             0.0   
48                  Charleston                0.0             0.0   
49                     Chelsea                0.0             0.0   
50                   Chinatown                0.0             0.0   
51                 City Island                0.0             0.0   
52                   City Line                0.0             0.0   
53                Civic Center                0.0             0.0   
54           Claremont Village                0.0             0.0   
55                Clason Point                0.0             0.0   
56                     Clifton                0.0             0.0   
57              

In [155]:
num_top_venues = 3

for hood in ny_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = ny_grouped[ny_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allerton----
               venue  freq
0        Pizza Place   0.2
1        Supermarket   0.1
2  Martial Arts Dojo   0.1


----Annadale----
          venue  freq
0  Dance Studio   0.1
1  Liquor Store   0.1
2         Diner   0.1


----Arden Heights----
         venue  freq
0     Pharmacy  0.25
1  Coffee Shop  0.25
2     Bus Stop  0.25


----Arlington----
                 venue  freq
0        Deli / Bodega   0.2
1          Coffee Shop   0.2
2  American Restaurant   0.2


----Arrochar----
                venue  freq
0  Italian Restaurant   0.2
1         Supermarket   0.1
2          Bagel Shop   0.1


----Arverne----
            venue  freq
0       Surf Spot   0.3
1  Sandwich Place   0.2
2      Board Shop   0.1


----Astoria----
                venue  freq
0                 Gym   0.2
1        Gourmet Shop   0.2
2  Mexican Restaurant   0.1


----Astoria Heights----
           venue  freq
0  Deli / Bodega   0.1
1     Laundromat   0.1
2          Plaza   0.1


----Auburndale----
          

Because tourists tend to go to different places, I find that the only top 3 venues were best fitted for this situation

In [156]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [157]:
num_top_venues = 3

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = ny_grouped['Neighborhood']

for ind in np.arange(ny_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(ny_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton           Pizza Place          Dessert Shop   
1       Annadale            Sports Bar          Liquor Store   
2  Arden Heights           Pizza Place           Coffee Shop   
3      Arlington         Deli / Bodega   American Restaurant   
4       Arrochar    Italian Restaurant         Deli / Bodega   

  3rd Most Common Venue  
0           Supermarket  
1          Dance Studio  
2              Pharmacy  
3         Grocery Store  
4           Pizza Place

In [158]:
# set number of clusters
nyclusters = 5

ny_grouped_clustering = ny_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=nyclusters, random_state=0).fit(ny_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([4, 1, 3, 0, 1, 4, 1, 1, 1, 1], dtype=int32)

In [163]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'cluster label', kmeans.labels_)

ny_merged = neighborhoods

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
ny_merged = ny_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

ny_merged.head() # check the last columns!

Borough Neighborhood     Latitude    Longitude  cluster label  Label  \
0   Bronx    Wakefield  40.89470518 -73.84720052            4.0    4.0   
1   Bronx   Co-op City  40.87429419 -73.82993911            4.0    4.0   
2   Bronx  Eastchester  40.88755568 -73.82780645            4.0    4.0   
3   Bronx    Fieldston  40.89543743 -73.90564260            1.0    1.0   
4   Bronx    Riverdale  40.89083449 -73.91258546            1.0    1.0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  
0            Food Truck            Donut Shop           Gas Station  
1        Mattress Store              Pharmacy        Ice Cream Shop  
2  Caribbean Restaurant                 Diner           Pizza Place  
3            Playground                 River                 Plaza  
4                  Park           Bus Station            Food Truck

### Cluster 1: Main Attraction
In this cluster we can see that is conformed by places of interest for tourists that come either alone or as a couple since there are lots of different 'Bodegas' and 'Cafes' in this group

In [164]:
ny_merged.loc[ny_merged['cluster label'] == 0, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood  Label 1st Most Common Venue   2nd Most Common Venue  \
28        Throgs Neck    0.0         Deli / Bodega          Baseball Field   
74           Canarsie    0.0         Deli / Bodega            Home Service   
77    Manhattan Beach    0.0                  Café                Bus Stop   
83        Marine Park    0.0         Deli / Bodega             Pizza Place   
85           Sea Gate    0.0          Optical Shop                   Beach   
150        Whitestone    0.0         Deli / Bodega                   Train   
171     Broad Channel    0.0         Deli / Bodega                Dive Bar   
172      Breezy Point    0.0                 Beach     Monument / Landmark   
178    Rockaway Beach    0.0                 Beach      Spanish Restaurant   
179          Neponsit    0.0                 Beach               Beach Bar   
190      Belle Harbor    0.0                 Beach      Mexican Restaurant   
191     Rockaway Park    0.0                 Beach                   Diner   
193        Brookville    0.0         Deli / Bodega             Yoga Studio   
194          Bellaire    0.0         Deli / Bodega        Greek Restaurant   
195      North Corona    0.0         Deli / Bodega    Gym / Fitness Center   
198      New Brighton    0.0              Bus Stop           Deli / Bodega   
204       South Beach    0.0         Deli / Bodega                    Pier   
206  Mariner's Harbor    0.0         Deli / Bodega      Italian Restaurant   
212           Oakwood    0.0              Bus Stop              Playground   
217       Tottenville    0.0           Frame Store  Thrift / Vintage Store   
224         Park Hill    0.0              Bus Stop             Coffee Shop   
227         Arlington    0.0         Deli / Bodega     American Restaurant   
232     Midland Beach    0.0                 Beach           Deli / Bodega   
234    New Dorp Beach    0.0         Deli / Bodega      Italian Restaurant   
238      Butler Manor    0.0                  Pool          Baseball Field   
258          Elm Park    0.0         Deli / Bodega     American Restaurant   
284     Manor Heights    0.0         Deli / Bodega              Bagel Shop   
285       Willowbrook    0.0              Bus Stop           Deli / Bodega   
288           Roxbury    0.0                 Beach               Irish Pub   
302           Hammels    0.0                 Beach              Food Truck   
305         Fox Hills    0.0         Deli / Bodega              Playground   

    3rd Most Common Venue  
28            Pizza Place  
74                    Gym  
77                   Food  
83           Soccer Field  
85                    Spa  
150         Moving Target  
171       Other Nightlife  
172           Supermarket  
178  Brazilian Restaurant  
179           Yoga Studio  
190                   Pub  
191    Seafood Restaurant  
193   Filipino Restaurant  
194    Chinese Restaurant  
195           Pizza Place  
198        Discount Store  
204                 Beach  
206        Nightlife Spot  
212                   Bar  
217        Cosmetics Shop  
224                 Hotel  
227         Grocery Store  
232              Bus Stop  
234            Sports Bar  
238              Bus Stop  
258            Toll Plaza  
284    Chinese Restaurant  
285          Intersection  
288                 Trail  
302                 Diner  
305        Sandwich Place

## Cluster 2: Family friendly
In this cluster we can see different venues for the likes of all family members. Parks, Spas, Playgrounds and restaurants makes this cluster the bes package option

In [165]:
ny_merged.loc[ny_merged['cluster label'] == 1, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood  Label      1st Most Common Venue  \
3                    Fieldston    1.0                 Playground   
4                    Riverdale    1.0                       Park   
6                  Marble Hill    1.0                Coffee Shop   
7                     Woodlawn    1.0        Rental Car Location   
12                 City Island    1.0         Seafood Restaurant   
24                 Hunts Point    1.0         Spanish Restaurant   
35              Spuyten Duyvil    1.0                       Park   
37                  Pelham Bay    1.0              Deli / Bodega   
39              Edgewater Park    1.0         Italian Restaurant   
46                   Bay Ridge    1.0                        Spa   
47                 Bensonhurst    1.0               Liquor Store   
49                  Greenpoint    1.0         Mexican Restaurant   
51              Brighton Beach    1.0          Food & Drink Shop   
52              Sheepshead Bay    1.0         Turkish Restaurant   
54                    Flatbush    1.0                Coffee Shop   
58             Windsor Terrace    1.0                       Café   
59            Prospect Heights    1.0                        Bar   
60                 Brownsville    1.0         Chinese Restaurant   
61                Williamsburg    1.0                        Bar   
62                    Bushwick    1.0                        Bar   
63          Bedford Stuyvesant    1.0                        Bar   
65                 Cobble Hill    1.0              Deli / Bodega   
66             Carroll Gardens    1.0                Coffee Shop   
67                    Red Hook    1.0             Ice Cream Shop   
68                     Gowanus    1.0      Performing Arts Venue   
69                 Fort Greene    1.0               Cocktail Bar   
70                  Park Slope    1.0     Furniture / Home Store   
76                 Mill Island    1.0                       Food   
79                  Bath Beach    1.0                       Park   
81               Dyker Heights    1.0                 Playground   
82             Gerritsen Beach    1.0                        Bar   
84                Clinton Hill    1.0                Yoga Studio   
86                    Downtown    1.0           Department Store   
87                 Boerum Hill    1.0                 Kids Store   
88   Prospect Lefferts Gardens    1.0                       Café   
93         Prospect Park South    1.0              Grocery Store   
95           East Williamsburg    1.0                        Bar   
96                  North Side    1.0             Pilates Studio   
99               Fort Hamilton    1.0         Italian Restaurant   
100                  Chinatown    1.0                     Museum   
101         Washington Heights    1.0                       Café   
102                     Inwood    1.0              Deli / Bodega   
103           Hamilton Heights    1.0                Yoga Studio   
104             Manhattanville    1.0           Ramen Restaurant   
105             Central Harlem    1.0                Music Venue   
106                East Harlem    1.0         Mexican Restaurant   
107            Upper East Side    1.0         Italian Restaurant   
108                  Yorkville    1.0                  Wine Shop   
109                 Lenox Hill    1.0           Czech Restaurant   
110           Roosevelt Island    1.0           Greek Restaurant   
111            Upper West Side    1.0              Movie Theater   
112             Lincoln Square    1.0                Opera House   
113                    Clinton    1.0                    Theater   
114                    Midtown    1.0        Sporting Goods Shop   
115                Murray Hill    1.0          Korean Restaurant   
116                    Chelsea    1.0             Ice Cream Shop   
117          Greenwich Village    1.0                       Café   
118               East Village    1.0        Moroccan Restaurant   
119   

## Cluster 3: Kids only
As you can see, this cluster is the perfect destination for families with small children 

In [167]:
ny_merged.loc[ny_merged['cluster label'] == 2, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood  Label 1st Most Common Venue 2nd Most Common Venue  \
27    Clason Point    2.0                  Park         Boat or Ferry   
192     Somerville    2.0                  Park           Yoga Studio   
203      Todt Hill    2.0                  Park           Yoga Studio   
256  Randall Manor    2.0              Bus Stop                  Park   
303      Bayswater    2.0                  Park            Playground   

    3rd Most Common Venue  
27         Scenic Lookout  
192  Fast Food Restaurant  
203  Fast Food Restaurant  
256           Pizza Place  
303  Ethiopian Restaurant

## Cluster 4: What you want to eat?
If the clients consider themselves as 'foodies' this is the perfect group for them. This cluster is filled with different food options

In [168]:
ny_merged.loc[ny_merged['cluster label'] == 3, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood  Label      1st Most Common Venue  \
5          Kingsbridge    3.0                Pizza Place   
8              Norwood    3.0                       Bank   
11      Pelham Parkway    3.0                Pizza Place   
13        Bedford Park    3.0                      Diner   
16             Fordham    3.0                      Diner   
17        East Tremont    3.0                Pizza Place   
32            Van Nest    3.0                Pizza Place   
33         Morris Park    3.0                Pizza Place   
34             Belmont    3.0              Deli / Bodega   
36     North Riverdale    3.0                Pizza Place   
40         Castle Hill    3.0                Pizza Place   
44           Unionport    3.0  Latin American Restaurant   
48         Sunset Park    3.0                Pizza Place   
50           Gravesend    3.0                     Lounge   
53   Manhattan Terrace    3.0                Pizza Place   
55       Crown Heights    3.0                     Museum   
64    Brooklyn Heights    3.0                Yoga Studio   
92             Midwood    3.0                Pizza Place   
97          South Side    3.0                Pizza Place   
136        Kew Gardens    3.0                Pizza Place   
137      Richmond Hill    3.0                Pizza Place   
142            Maspeth    3.0                      Diner   
176           Edgemere    3.0                Pizza Place   
208  Castleton Corners    3.0                Pizza Place   
213        Great Kills    3.0                Pizza Place   
214        Eltingville    3.0           Sushi Restaurant   
231       Dongan Hills    3.0         Italian Restaurant   
240          Rossville    3.0                 Bagel Shop   
241      Arden Heights    3.0                Pizza Place   
242         Greenridge    3.0                Pizza Place   
246         Bulls Head    3.0            Thai Restaurant   
253            Clifton    3.0              Grocery Store   
260           New Lots    3.0                Pizza Place   
262         Mill Basin    3.0                 Bagel Shop   
291       Prince's Bay    3.0                Pizza Place   

         2nd Most Common Venue 3rd Most Common Venue  
5                          Pub              Beer Bar  
8                  Pizza Place                  Park  
11          Chinese Restaurant        Ice Cream Shop  
13                 Pizza Place         Deli / Bodega  
16                         Gym  Gym / Fitness Center  
17              Breakfast Spot     Mobile Phone Shop  
32               Deli / Bodega        Cosmetics Shop  
33               Deli / Bodega          Burger Joint  
34          Italian Restaurant          Dessert Shop  
36          Mexican Restaurant                  Pool  
40               Deli / Bodega    Spanish Restaurant  
44                      Lounge    Spanish Restaurant  
48   Latin American Restaurant        Ice Cream Shop  
50                 Pizza Place                Bakery  
53                  Steakhouse        Cosmetics Shop  
55                 Pizza Place                  Café  
64                       Diner      Sushi Restaurant  
92              Ice Cream Shop    Italian Restaurant  
97            Tapas Restaurant              Wine Bar  
136          Indian Restaurant             Juice Bar  
137  Latin American Restaurant  Gym / Fitness Center  
142                Pizza Place            Sports Bar  
176                       Farm    Seafood Restaurant  
208                  Mini Golf        Ice Cream Shop  
213                        Bar    Chinese Restaurant  
214                Pizza Place                   Gym  
231                Pizza Place              Pharmacy  
240                Pizza Place          Liquor Store  
241                Coffee Shop              Pharmacy  
242                   Bus Stop            Bagel Shop  
246                Wings Joint    Tex-Mex Restaurant  
253                Pizza Place         Deli / Bodega  
260             Breakfast Spot    

## Cluster 5: NY and chill
This group is for all kind of tourists since it offers different restaurants, bars and other types of entertainment. 

In [169]:
ny_merged.loc[ny_merged['cluster label'] == 4, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood  Label            1st Most Common Venue  \
0              Wakefield    4.0                       Food Truck   
1             Co-op City    4.0                   Mattress Store   
2            Eastchester    4.0             Caribbean Restaurant   
9         Williamsbridge    4.0             Caribbean Restaurant   
10            Baychester    4.0             Gym / Fitness Center   
14    University Heights    4.0                    Grocery Store   
15        Morris Heights    4.0               Spanish Restaurant   
18            West Farms    4.0                             Park   
19          High  Bridge    4.0                         Pharmacy   
20               Melrose    4.0                       Donut Shop   
21            Mott Haven    4.0                       Donut Shop   
22           Port Morris    4.0                          Brewery   
23              Longwood    4.0             Fast Food Restaurant   
25            Morrisania    4.0                   Discount Store   
26             Soundview    4.0                    Grocery Store   
29          Country Club    4.0                   Sandwich Place   
30           Parkchester    4.0               Mexican Restaurant   
31    Westchester Square    4.0                    Indie Theater   
38         Schuylerville    4.0               Mexican Restaurant   
41             Olinville    4.0             Caribbean Restaurant   
42        Pelham Gardens    4.0                         Pharmacy   
43             Concourse    4.0               Spanish Restaurant   
45              Edenwald    4.0                      Bus Station   
56         East Flatbush    4.0                             Park   
57            Kensington    4.0                  Thai Restaurant   
71         Cypress Hills    4.0                   Ice Cream Shop   
72         East New York    4.0               Chinese Restaurant   
73         Starrett City    4.0                      Supermarket   
75             Flatlands    4.0             Caribbean Restaurant   
78          Coney Island    4.0             Caribbean Restaurant   
80          Borough Park    4.0                             Bank   
89            Ocean Hill    4.0               Chinese Restaurant   
90             City Line    4.0                             Bank   
91          Bergen Beach    4.0                  Harbor / Marina   
94            Georgetown    4.0                       Donut Shop   
98         Ocean Parkway    4.0                       Steakhouse   
141        East Elmhurst    4.0                       Donut Shop   
146            Woodhaven    4.0                         Pharmacy   
147           Ozone Park    4.0                              Gym   
148     South Ozone Park    4.0             Fast Food Restaurant   
149        College Point    4.0                       Donut Shop   
154           Douglaston    4.0                       Donut Shop   
155            Glen Oaks    4.0                    Grocery Store   
156            Bellerose    4.0                    Deli / Bodega   
157    Kew Gardens Hills    4.0                             Bank   
158        Fresh Meadows    4.0                      Bus Station   
162       Queens Village    4.0                             Bank   
163               Hollis    4.0                   Sandwich Place   
164        South Jamaica    4.0                      Bus Station   
165           St. Albans    4.0             Caribbean Restaurant   
166             Rochdale    4.0  Southern / Soul Food Restaurant   
167  Springfield Gardens    4.0                       Donut Shop   
168      Cambria Heights    4.0             Caribbean Restaurant   
169             Rosedale    4.0                Accessories Store   
170         Far Rockaway    4.0               Chinese Restaurant   
173             Steinway    4.0                        Irish Pub   
174           Beechhurst    4.0                    Deli / Bodega   
177              Arverne    4.0                        Surf Spot   


## LA Clusters
Now, we proceed to do the same process in Los Angeles as we did in New York

In [74]:
venues_la = getNearbyVenues(names = df['Neighborhood'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )

Chinatown
Civic Center
Fashion District
Financial District
Historic Core
Jewerly District
Little Tokyo
Skid Row
South Park
Old Bank
Toy District
Wholesale
Harbor City
Harbor Gateway
San Pedro
Terminal Island
Wilmington
Beechwood Canyon
Franklin Hills
Hollywood
East Hollywood
Hollywood Hills
Laurel Canyon
Little Armenia
Los Feliz
Melrose District
Mount Olympus
Sierra Vista
Sunset Strip
Spaulding Square
Thai Town
Yucca Corridor
Brookside Park
Carthay Circle
Country Club Park
Fairfax District
Fremont Place
Hancock Park
Harvard Heights
Koreatown
Larchmont
Miracle Mile
Olympic Park
Park La Brea
Park Mile
Picfair Village
Wellington Square
Western Heights
Wilshire Center
Wilshire Vista
Windsor Square
Angelino Heights 
Echo Park 
Historic Filipinotown 
Lafayette Park 
MacArthur Park 
Pico-Union 
Silver Lake 
Sunset Junction 
Temple-Beaudry 
Westlake 
Virgil Village
Aliso Village 
Arroyo Seco 
Atwater Village 
Cypress Park 
Boyle Heights 
Eagle Rock 
El Sereno 
Elysian Park 
Elysian Valley 
Gar

In [75]:
print(venues_la.shape)
venues_la.head()

(1299, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Chinatown              34.064989             -118.237295   
1    Chinatown              34.064989             -118.237295   
2    Chinatown              34.064989             -118.237295   
3    Chinatown              34.064989             -118.237295   
4    Chinatown              34.064989             -118.237295   

               Venue  Venue Latitude  Venue Longitude         Venue Category  
0        Burgerlords     34.06530281    -118.23724485           Burger Joint  
1  Blossom Chinatown     34.06565301    -118.23743473  Vietnamese Restaurant  
2             Pho 87     34.06725753    -118.23557436  Vietnamese Restaurant  
3      General Lee's     34.06577774    -118.23757667                    Bar  
4      Melody Lounge     34.06559250    -118.23813640                    Bar

In [76]:
venues_la.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                                
Aliso Village                                  10                      10   
Angelino Heights                               10                      10   
Arleta                                          1                       1   
Arroyo Seco                                    10                      10   
Athens Park                                     6                       6   
Atwater Village                                10                      10   
Balboa Park                                    10                      10   
Baldwin Hills                                   1                       1   
Baldwin Village                                 4                       4   
Baldwin Vista                                   5                       5   
Beechwood Canyon                                8                       8   
Bel-Air                                         1                       1   
Benedict Canyon                                 6                       6   
Beverly Crest                                   2                       2   
Beverly Glen                                    1                       1   
Beverlywood                                     4                       4   
Boyle Heights                                  10                      10   
Brentwood                                      10                      10   
Brookside Park                                  8                       8   
Cahuenga Pass                                  10                      10   
Canoga Park                                     9                       9   
Carthay Circle                                 10                      10   
Castellammare                                   8                       8   
Century City                                   10                      10   
Chatsworth                                      4                       4   
Chesterfield Square                             6                       6   
Cheviot Hills                                   5                       5   
Chinatown                                      10                      10   
Civic Center                                   10                      10   
Country Club Park                              10                      10   
Crenshaw                                       10                      10   
Crestview                                       5                       5   
Cypress Park                                    4                       4   
Eagle Rock                                     10                      10   
East Hollywood                                 10                      10   
Echo Park                                      10                      10   
El Sereno                                       2                       2   
Elysian Park                                    9                       9   
Elysian Valley                                 10                      10   
Encino                                          6                       6   
Exposition Park                                10                      10   
Fairfax District                               10                      10   
Fashion District                               10                      10   
Financial District                             10                      10   
Franklin Hills                                 10                      10   
Fremont Place                                   2                       2   
Garvanza                                        7                       7   
Glassell Park                                   4                       4   
Gramercy Park                                   6                       6   
Granada Hills                                   3                       3   
Hancock Park            

In [77]:
la_onehot = pd.get_dummies(venues_la[['Venue Category']], prefix="", prefix_sep="")


la_onehot['Neighborhood'] = venues_la['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [la_onehot.columns[-1]] + list(la_onehot.columns[:-1])
la_onehot = la_onehot[fixed_columns]

la_onehot.head()

Yoga Studio  ATM  Accessories Store  Adult Boutique  American Restaurant  \
0            0    0                  0               0                    0   
1            0    0                  0               0                    0   
2            0    0                  0               0                    0   
3            0    0                  0               0                    0   
4            0    0                  0               0                    0   

   Amphitheater  Arcade  Argentinian Restaurant  Art Gallery  Art Museum  \
0             0       0                       0            0           0   
1             0       0                       0            0           0   
2             0       0                       0            0           0   
3             0       0                       0            0           0   
4             0       0                       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0                    0                 0                   0   
1                    0                 0                   0   
2                    0                 0                   0   
3                    0                 0                   0   
4                    0                 0                   0   

   Australian Restaurant  Auto Garage  Auto Workshop  Automotive Shop  \
0                      0            0              0                0   
1                      0            0              0                0   
2                      0            0              0                0   
3                      0            0              0                0   
4                      0            0              0                0   

   BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  Basketball Court  \
0          0           0       0     0    0               0                 0   
1          0           0       0     0    0               0                 0   
2          0           0       0     0    0               0                 0   
3          0           0       0     0    1               0                 0   
4          0           0       0     0    1               0                 0   

   Basketball Stadium  Bed & Breakfast  Beer Garden  Beer Store  \
0                   0                0            0           0   
1                   0                0            0           0   
2                   0                0            0           0   
3                   0                0            0           0   
4                   0                0            0           0   

   Big Box Store  Bike Shop  Bistro  Bookstore  Botanical Garden  Boutique  \
0              0          0       0          0                 0         0   
1              0          0       0          0                 0         0   
2              0          0       0          0                 0         0   
3              0          0       0          0                 0         0   
4              0          0       0          0                 0         0   

   Boxing Gym  Breakfast Spot  Brewery  Bridge  Bubble Tea Shop  Burger Joint  \
0           0               0        0       0                0             1   
1           0               0        0       0                0             0   
2           0               0        0       0                0             0   
3           0               0        0       0                0             0   
4           0               0        0       0                0             0   

   Burrito Place  Bus Station  Business Service  Butcher  Cable Car  Café  \
0              0            0                 0        0          0     0   
1              0            0                 0        0          0     0   
2              0            0                 0        0          0     0   
3              0            0                 0        0          0     0   
4              0

In [78]:
la_grouped = la_onehot.groupby('Neighborhood').mean().reset_index()
la_grouped

Neighborhood  Yoga Studio  ATM  Accessories Store  \
0                Aliso Village    0.00000000  0.0         0.00000000   
1             Angelino Heights    0.00000000  0.0         0.00000000   
2                       Arleta    0.00000000  0.0         0.00000000   
3                  Arroyo Seco    0.00000000  0.0         0.00000000   
4                  Athens Park    0.00000000  0.0         0.00000000   
5              Atwater Village    0.00000000  0.0         0.00000000   
6                  Balboa Park    0.00000000  0.0         0.00000000   
7                Baldwin Hills    0.00000000  0.0         0.00000000   
8              Baldwin Village    0.00000000  0.0         0.00000000   
9                Baldwin Vista    0.00000000  0.0         0.00000000   
10             Beechwood Canyon   0.00000000  0.0         0.00000000   
11                     Bel-Air    0.00000000  0.0         0.00000000   
12             Benedict Canyon    0.00000000  0.0         0.16666667   
13               Beverly Crest    0.00000000  0.0         0.00000000   
14                Beverly Glen    0.00000000  0.0         0.00000000   
15                 Beverlywood    0.00000000  0.0         0.00000000   
16               Boyle Heights    0.00000000  0.0         0.00000000   
17                   Brentwood    0.00000000  0.0         0.00000000   
18               Brookside Park   0.00000000  0.0         0.00000000   
19               Cahuenga Pass    0.00000000  0.0         0.00000000   
20                 Canoga Park    0.00000000  0.0         0.00000000   
21               Carthay Circle   0.00000000  0.0         0.00000000   
22               Castellammare    0.00000000  0.0         0.00000000   
23                Century City    0.00000000  0.0         0.00000000   
24                  Chatsworth    0.00000000  0.0         0.00000000   
25         Chesterfield Square    0.00000000  0.0         0.00000000   
26               Cheviot Hills    0.00000000  0.0         0.00000000   
27                    Chinatown   0.00000000  0.0         0.00000000   
28                 Civic Center   0.00000000  0.0         0.00000000   
29            Country Club Park   0.00000000  0.0         0.00000000   
30                    Crenshaw    0.00000000  0.0         0.00000000   
31                   Crestview    0.00000000  0.0         0.00000000   
32                Cypress Park    0.00000000  0.0         0.00000000   
33                  Eagle Rock    0.10000000  0.0         0.00000000   
34               East Hollywood   0.00000000  0.0         0.00000000   
35                   Echo Park    0.00000000  0.0         0.00000000   
36                   El Sereno    0.00000000  0.0         0.00000000   
37                Elysian Park    0.00000000  0.0         0.00000000   
38              Elysian Valley    0.00000000  0.0         0.00000000   
39                      Encino    0.00000000  0.0         0.00000000   
40             Exposition Park    0.00000000  0.0         0.00000000   
41             Fairfax District   0.00000000  0.0         0.00000000   
42             Fashion District   0.00000000  0.0         0.00000000   
43           Financial District   0.00000000  0.0         0.00000000   
44               Franklin Hills   0.00000000  0.0         0.00000000   
45                Fremont Place   0.00000000  0.0         0.00000000   
46                    Garvanza    0.00000000  0.0         0.00000000   
47               Glassell Park    0.00000000  0.0         0.00000000   
48               Gramercy Park    0.00000000  0.0         0.00000000   
49               Granada Hills    0.00000000  0.0         0.00000000   
50                 Hancock Park   0.00000000  0.0         0.00000000   
51                  Harbor City   0.00000000  0.0         0.00000000   
52               Harbor Gateway   0.00000000  0.0         0.00000000   
53              Harvard Heights   0.00000000  0.0         0.00000000   
54               Highland Park    0.00000000  0.0         0

In [79]:
num_top_venues_la = 5

for hood_la in la_grouped['Neighborhood']:
    print("----"+hood_la+"----")
    temp = la_grouped[la_grouped['Neighborhood'] == hood_la].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Aliso Village ----
            venue  freq
0          Bridge   0.1
1  Clothing Store   0.1
2    Cycle Studio   0.1


----Angelino Heights ----
                 venue  freq
0  Japanese Restaurant   0.2
1        Hot Dog Joint   0.1
2           Beer Store   0.1


----Arleta ----
               venue  freq
0         Taco Place   1.0
1        Yoga Studio   0.0
2  Other Repair Shop   0.0


----Arroyo Seco ----
          venue  freq
0  Liquor Store   0.1
1  Dessert Shop   0.1
2      Wine Bar   0.1


----Athens Park ----
                  venue  freq
0    Mexican Restaurant  0.17
1     Convenience Store  0.17
2  Fast Food Restaurant  0.17


----Atwater Village ----
                      venue  freq
0              Liquor Store   0.1
1            Farmers Market   0.1
2  Mediterranean Restaurant   0.1


----Balboa Park ----
                venue  freq
0  Mexican Restaurant   0.2
1   Convenience Store   0.1
2      Sandwich Place   0.1


----Baldwin Hills ----
               venue  freq
0      

In [109]:
num_top_venues = 3

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind1 in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind1+1, indicators[ind1]))
    except:
        columns.append('{}th Most Common Venue'.format(ind1+1))

# create a new dataframe
neighborhoods_venuesLA_sorted = pd.DataFrame(columns=columns)
neighborhoods_venuesLA_sorted['Neighborhood'] = la_grouped['Neighborhood']

for ind1 in np.arange(la_grouped.shape[0]):
    neighborhoods_venuesLA_sorted.iloc[ind1, 1:] = return_most_common_venues(la_grouped.iloc[ind1, :], num_top_venues)

neighborhoods_venuesLA_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0     Aliso Village       Storage Facility               Brewery   
1  Angelino Heights    Japanese Restaurant           Coffee Shop   
2            Arleta             Taco Place           Wings Joint   
3       Arroyo Seco           Dessert Shop  Gym / Fitness Center   
4       Athens Park             Food Truck  Fast Food Restaurant   

  3rd Most Common Venue  
0                Bridge  
1        Sandwich Place  
2        Discount Store  
3                 Diner  
4    Mexican Restaurant

In [110]:
kclusters = 5

la_grouped_clustering = la_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(la_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 2, 1, 1, 1, 2, 1, 1, 1, 1], dtype=int32)

In [111]:
# add clustering labels
neighborhoods_venuesLA_sorted.insert(0, 'Label Cluster', kmeans.labels_)

la_merged = LA_data

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
la_merged = la_merged.join(neighborhoods_venuesLA_sorted.set_index('Neighborhood'), on='Neighborhood')

la_merged.head() # check the last columns!

Borough        Neighborhood   Latitude   Longitude  \
0  Downtown Los Angeles            Chinatown  34.064989 -118.237295   
1  Downtown Los Angeles         Civic Center  34.056096 -118.244619   
2  Downtown Los Angeles     Fashion District  34.037529 -118.250216   
3  Downtown Los Angeles   Financial District  34.048893 -118.258459   
4  Downtown Los Angeles        Historic Core  34.044376 -118.251475   

   Label Cluster 1st Most Common Venue  2nd Most Common Venue  \
0            2.0                Bakery  Vietnamese Restaurant   
1            1.0               Theater            High School   
2            2.0        Breakfast Spot            Coffee Shop   
3            2.0      Sushi Restaurant           Cupcake Shop   
4            2.0                   Bar            Coffee Shop   

  3rd Most Common Venue  
0                   Bar  
1                 Plaza  
2         Movie Theater  
3           Pizza Place  
4           Music Venue

## Cluster 1: For the family
Filled with parks, museums and restaurants; this is perfect for the entire family

In [112]:
la_merged.loc[la_merged['Label Cluster'] == 0, la_merged.columns[[1] + list(range(5, la_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
68           El Sereno     Chinese Restaurant                  Park   
76   Montecito Heights         History Museum                  Park   
88    Lakeview Terrace            Record Shop                  Park   
89         Lake Balboa                   Park            Playground   
91       Mission Hills                   Park                 Plaza   
98       Panorama City                   Park           Wings Joint   
131     Jefferson Park                 Market                  Park   
137       View Heights           Concert Hall                  Park   
139       Vermont Park          Auto Workshop          Burger Joint   
148        Beverlywood           Concert Hall         Burrito Place   

    3rd Most Common Venue  
68            Wings Joint  
76   Fast Food Restaurant  
88                  Diner  
89    American Restaurant  
91                 Garden  
98              Disc Golf  
131           Wings Joint  
137           Wings Joint  
139                  Park  
148                  Park

## Cluster 2: Some 'Me' time
This group is represented with places for people who want to have some alone time while relaxing in different places

In [170]:
la_merged.loc[la_merged['Label Cluster'] == 1, la_merged.columns[[1] + list(range(5, la_merged.shape[1]))]]

Neighborhood      1st Most Common Venue  \
1                  Civic Center                    Theater   
5              Jewerly District                    Theater   
7                      Skid Row                Art Gallery   
8                    South Park                        Spa   
12                  Harbor City       Fast Food Restaurant   
13               Harbor Gateway                Bus Station   
14                    San Pedro        American Restaurant   
16                   Wilmington        American Restaurant   
19                    Hollywood              Burrito Place   
20               East Hollywood  Middle Eastern Restaurant   
22                Laurel Canyon                Music Venue   
23               Little Armenia         Mexican Restaurant   
25             Melrose District                Pizza Place   
30                    Thai Town              Historic Site   
32               Brookside Park                     Museum   
34            Country Club Park          Korean Restaurant   
36                Fremont Place                   Wine Bar   
38              Harvard Heights          Mobile Phone Shop   
39                    Koreatown          Korean Restaurant   
41                 Miracle Mile                 Food Truck   
42                 Olympic Park       Ethiopian Restaurant   
46            Wellington Square             Cosmetics Shop   
47              Western Heights                 Taco Place   
48              Wilshire Center          Korean Restaurant   
49               Wilshire Vista       Ethiopian Restaurant   
52                   Echo Park                  Food Truck   
53       Historic Filipinotown        Fast Food Restaurant   
54              Lafayette Park           Korean Restaurant   
55              MacArthur Park                         Spa   
56                  Pico-Union                  Taco Place   
59              Temple-Beaudry        Fast Food Restaurant   
60                    Westlake              Discount Store   
63                 Arroyo Seco                Dessert Shop   
66               Boyle Heights          Mexican Restaurant   
69                Elysian Park             Other Nightlife   
71                    Garvanza      Gluten-free Restaurant   
72               Glassell Park                        Café   
74            Hillside Village        Fast Food Restaurant   
75             Lincoln Heights        Fast Food Restaurant   
78              Mt. Washington              Scenic Lookout   
80                      Arleta                  Taco Place   
81                 Balboa Park          Mexican Restaurant   
82               Cahuenga Pass                 Beer Garden   
83                 Canoga Park          Mexican Restaurant   
84                  Chatsworth                Home Service   
85                      Encino      Furniture / Home Store   
86               Granada Hills        Gym / Fitness Center   
92          NoHo Arts District               Movie Theater   
93                 North Hills        Fast Food Restaurant   
94             North Hollywood          Mexican Restaurant   
96                  Olive View                    Hospital   
97                     Pacoima        Fast Food Restaurant   
100                     Reseda       Vietnamese Restaurant   
102               Shadow Hills              Pilates Studio   
104                Studio City                   BBQ Joint   
105                 Sun Valley           Electronics Store   
107                     Sylmar                      Museum   
108                    Tarzana      Furniture / Home Store   
110               Toluca Woods                 Pizza Place   
112             Universal City                  Theme Park   
113                Valley Glen                 Pizza Place   
114             Valley Village        Fast Food Restaurant   
115                   Van Nuys   Latin American Restaurant   
116  Ventura Business District             Thai Res

## Cluster 3: Fit and delicious
This group is filled with food options and different gym and sports options for the people that like 'that healthy lifestyle' but also enjoy good food

In [114]:
la_merged.loc[la_merged['Label Cluster'] == 2, la_merged.columns[[1] + list(range(5, la_merged.shape[1]))]]

Neighborhood          1st Most Common Venue  \
0               Chinatown                         Bakery   
2        Fashion District                 Breakfast Spot   
3      Financial District               Sushi Restaurant   
4           Historic Core                            Bar   
6            Little Tokyo                            Bar   
9                Old Bank               Sushi Restaurant   
10           Toy District               Sushi Restaurant   
11              Wholesale             Italian Restaurant   
18         Franklin Hills                     Restaurant   
24              Los Feliz                    Coffee Shop   
26          Mount Olympus           Gym / Fitness Center   
27           Sierra Vista                Thai Restaurant   
28           Sunset Strip                       Boutique   
29       Spaulding Square                            Gym   
31         Yucca Corridor                            Bar   
33         Carthay Circle                    Coffee Shop   
35       Fairfax District                           Café   
40              Larchmont                    Coffee Shop   
43           Park La Brea                     Boxing Gym   
44              Park Mile            Japanese Restaurant   
45        Picfair Village           Fast Food Restaurant   
50         Windsor Square                 Ice Cream Shop   
51      Angelino Heights             Japanese Restaurant   
57           Silver Lake                  Ice Cream Shop   
58       Sunset Junction                      Comic Shop   
61         Virgil Village                       Boutique   
62         Aliso Village                Storage Facility   
64       Atwater Village        Mediterranean Restaurant   
67            Eagle Rock                       Wine Shop   
70        Elysian Valley                  Sandwich Place   
73         Highland Park              Mexican Restaurant   
79      University Hills                       Gastropub   
87             Knollwood                      Sports Bar   
95            Northridge              Mexican Restaurant   
99          Porter Ranch                    Liquor Store   
103         Sherman Oaks                     Yoga Studio   
106              Sunland              Mexican Restaurant   
109          Toluca Lake                Sushi Restaurant   
111              Tujunga                    Liquor Store   
117        Warner Center                      Steakhouse   
119          West Toluca   Vegetarian / Vegan Restaurant   
121       Woodland Hills                  Ice Cream Shop   
133         Leimert Park               Convenience Store   
135    Nickerson Gardens                       Rock Club   
136      University Park                  Breakfast Spot   
138       Vermont Knolls                      Shoe Store   
141                Watts                    Home Service   
149            Brentwood              Italian Restaurant   
156  Palisades Highlands                        Boutique   
157          Rancho Park                      Restaurant   
161     Westside Village                     Yoga Studio   
162             Westwood                           Hotel   
163       Loyola Village              Mexican Restaurant   
164    Manchester Square             Fried Chicken Joint   
166              Oakwood                        Boutique   
167                Palms                            Café   
168        Playa del Rey                   Deli / Bodega   
169          Playa Vista                     Yoga Studio   
172              Westdale                            Gym   

             2nd Most Common Venue    3rd Most Common Venue  
0            Vietnamese Restaurant                      Bar  
2                      Coffee Shop            Movie Theater  
3                     Cupcake Shop              Pizza Place  
4                      Coffee Shop              Music Venue  
6                            Plaza              Coffee Shop  
9               Mexican Restaurant      

## Cluster 4 = Deep breath of mother nature
This is perfect for more adventurous tourists who want to take a break from all the noise of the city

In [115]:
la_merged.loc[la_merged['Label Cluster'] == 3, la_merged.columns[[1] + list(range(5, la_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
17     Beechwood Canyon                 Trail            Campground   
21      Hollywood Hills                 Trail      Sculpture Garden   
65        Cypress Park                  Trail        Scenic Lookout   
77      Monterey Hills                  Trail              Wine Bar   
147       Beverly Glen                  Trail           Wings Joint   
155  Pacific Palisades     Athletics & Sports                 Trail   

    3rd Most Common Venue  
17   Gym / Fitness Center  
21         Scenic Lookout  
65                   Park  
77                   Pool  
147             Disc Golf  
155            Food Truck

## Cluster 5: For the classic ones
This small group is for tourist who want to feel a little bit classy and relax while playing some golf

In [116]:
la_merged.loc[la_merged['Label Cluster'] == 4, la_merged.columns[[1] + list(range(5, la_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
37   Hancock Park           Golf Course           Wings Joint   
101    Sepulveda            Golf Course           Coffee Shop   

    3rd Most Common Venue  
37              Disc Golf  
101        Baseball Field

## MAPS
In this section we will be comparing how the clusters form in each city and determine if there are similarities among these two 'different' places

In [92]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [133]:
ny_merged.dropna(axis = 0, how = 'any', inplace = True)

In [135]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(nyclusters)
ys = [i + x + (i*x)**2 for i in range(nyclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, Cluster in zip(ny_merged['Latitude'], ny_merged['Longitude'], ny_merged['Neighborhood'], ny_merged['Labels'].astype(int)):
    label = folium.Popup(str(poi) + ' Cluster ' + str(Cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[Cluster-1],
        fill=True,
        fill_color=rainbow[Cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [149]:
address_la = 'Los Angeles, CA'

geolocator = Nominatim(user_agent="LA_explorer")
location_la = geolocator.geocode(address_la)
latitude_la = location.latitude
longitude_la = location.longitude


In [150]:
map_la = folium.Map(location=[latitude_la, longitude_la], zoom_start=10)

# add markers to map
for lat_la, lng_la, borough_la, neighborhood_la in zip(LA_data['Latitude'], LA_data['Longitude'], LA_data['Borough'], LA_data['Neighborhood']):
    label1 = '{}, {}'.format(neighborhood_la, borough_la)
    label2 = folium.Popup(label1, parse_html=True)
    folium.CircleMarker(
        [lat_la, lng_la],
        radius=5,
        popup=label2,
        color='yellow',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_la)  
    
map_la

In [151]:
la_merged.dropna(axis = 0, how = 'any', inplace = True)

In [154]:
# create map
map_clusters_LA = folium.Map(location=[latitude_la, longitude_la], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(la_merged['Latitude'], la_merged['Longitude'], la_merged['Neighborhood'], la_merged['Label Cluster'].astype(int)):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters_LA)
       
map_clusters_LA